In [3]:
import pandas as pd
from database import connect_to_db, format_sql
import plotly.graph_objects as go
from sqlalchemy import text, create_engine
import numpy as np
from dotenv import load_dotenv
from os import getenv
import psycopg2

In [4]:
detector_name_og = 'Abuja'
detector_name = detector_name_og.lower()

# Format detector name to lowercase and check formatting of name 
# doesn't have number up front
detector_name = detector_name_og.lower()
if detector_name.startswith('2') or detector_name.startswith('4'):
    detector_name = detector_name[1:]+detector_name[0]

detectors = pd.read_csv('detector_info_settings/detector_locations.csv', sep=',')
detector_station = detectors.loc[detectors['name'] == detector_name_og, 'weather_station'].item()
detector_station = detector_station.lower()
detector_name, detector_station

('abuja', 'dnaa')

In [5]:
db = connect_to_db()

with db.connect() as conn:
    query = text(f'SELECT * FROM {detector_name}')
    result = conn.execute(query)
    counts_data = result.fetchall()
    conn.close()
    
    db = connect_to_db()
    with db.connect() as conn:

        query = text(f'SELECT * FROM {detector_station}')
        result = conn.execute(query)
        weather_data = result.fetchall()
        conn.close()

        # Format data into pandas df
        df = format_sql(counts_data)
        wdf = format_sql(weather_data)
        print(wdf.dtypes.to_list())
        # print(wdf)

        df.index = df.index.tz_localize(None)

    # Close connection
    db.dispose()

Connected to muon database successfully
Connected to muon database successfully
None
None
[dtype('float64'), dtype('float64'), dtype('float64')]


In [4]:
df.head(1), df.tail(1), wdf.head(1), wdf.tail(1)

(                     counts  hourly_mov_average
 date                                           
 2023-08-15 23:00:00  4851.0              4851.0,
                      counts  hourly_mov_average
 date                                           
 2024-08-24 17:00:00  7566.0         7459.666667,
                      temp_in_f  sea_l_pressure_millibar  alti_pressure
 date                                                                  
 2023-08-15 23:00:00       89.6                      NaN          29.77,
                      temp_in_f  sea_l_pressure_millibar  alti_pressure
 date                                                                  
 2024-09-08 23:00:00       84.2                      NaN           29.8)

In [36]:
columns_types = wdf.dtypes.to_list()
if len(set(columns_types)) > 1:
    for col in wdf.columns.to_list():
        wdf[col] = pd.to_numeric(wdf[col])

In [72]:
df.loc[(df['counts'] > df['counts'].mean() + (4*df['counts'].std())) | (df['counts'] < df['counts'].mean() - (4*df['counts'].std()))] = np.nan

In [70]:
wdf.loc[(wdf['alti_pressure'] > wdf['alti_pressure'].mean() + (4*wdf['alti_pressure'].std())) | (wdf['alti_pressure'] < wdf['alti_pressure'].mean() - (4*wdf['alti_pressure'].std()))] = np.nan

In [123]:
df.sort_index(inplace=True)
# Calculate hourly moving average
df['hourly_mov_average'] = df['counts'].rolling(window='24h').mean()

In [121]:
f = df.index.get_loc(df.first_valid_index())
l = df.index.get_loc(df.isna().idxmax().head(1).values[0])
print(f, l)

while l <= len(df) and f != l:
    # Deal with spikes after shutdowns
    if (f+24) < l:
        mean = df[f:(f+24)].mean().values[0]
        std = df[f:(f+24)].std().values[0]
    else:
        mean = df[f:(l - 1)].mean().values[0]
        std = df[f:(l - 1)].std().values[0]
    print(mean, std)
    if df.iloc[f]['counts'] == 6948.0:
        print('****************', df.iloc[f+1]['counts'])
    if df.iloc[f]['counts'] < (mean - (std*1.5)) or df.iloc[f]['counts'] > (mean + (std*2)):
        df.iloc[f]['counts'] = np.nan
    if df.iloc[f+1]['counts'] < (mean - (std*1.5)) or df.iloc[f+2]['counts'] > (mean + (std*2)):
        df.iloc[(f+1)]['counts'] = np.nan
    if df.iloc[f+2]['counts'] < (mean - (std*1.5)) or df.iloc[f+2]['counts'] > (mean + (std*2)):
        df.iloc[(f+2)]['counts'] = np.nan

    # Deal with spikes before shutdowns
    if (l-25) > f:
        mean = df[(l - 25):(l - 1)].mean().values[0]
        std = df[(l - 25):(l - 1)].std().values[0]
    else:
        mean = df[f:(l - 1)].mean().values[0]
        std = df[f:(l - 1)].std().values[0]
    print(mean, std, std*2)

    if df.iloc[l-1]['counts'] < (mean - (std*1.5)) or df.iloc[l-1]['counts'] > (mean + (std*2)):
        df.iloc[(l-1)]['counts'] = np.nan
    if df.iloc[l-2]['counts'] < (mean - (std*1.5)) or df.iloc[l-2]['counts'] > (mean + (std*2)):
        df.iloc[(l-2)]['counts'] = np.nan
    if df.iloc[l-3]['counts'] < (mean - (std*1.5)) or df.iloc[l-3]['counts'] > (mean + (std*2)):
        df.iloc[(l-3)]['counts'] = np.nan

    f = df.index.get_loc(df[l:].first_valid_index())
    l = df.index.get_loc(df[f:].isna().idxmax().head(1).values[0])
    print('new: ', f, l)

    if l == f:
        break

0 17
6108.1875 600.0421339372762
6192.0 515.1192649696351 1030.2385299392702
new:  18 138
9719.375 1270.815342947025
10002.0 632.3698697549663 1264.7397395099326
new:  141 308
9764.5 1183.2519669923665
9481.791666666666 513.6315697976066 1027.2631395952133
new:  310 331
9263.55 590.3802944757415
9385.0 237.7428582874082 475.4857165748164
new:  4199 4626
9251.541666666666 108.51005930794845
8893.541666666666 85.94081844712859 171.88163689425718
new:  4628 4637
8500.375 222.59311855619308
8500.375 222.59311855619308 445.18623711238615
new:  4639 4645
8814.4 28.693204770467865
8814.4 28.693204770467865 57.38640954093573
new:  4648 4651
8748.0 15.556349186104045
8748.0 15.556349186104045 31.11269837220809
new:  4653 4966
8707.25 110.74382895752663
8734.791666666666 100.18937684147984 200.37875368295968
new:  5251 5684
8707.208333333334 122.82896527344406
8534.125 112.71522890047713 225.43045780095426
new:  5686 5821
8594.333333333334 709.3018408613327
**************** 5944.0
8678.833333333

/var/folders/tg/f26try5n4pq7thttks3b9fs00000gn/T/ipykernel_44868/776011527.py:17: FutureWarning:

ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


/var/folders/tg/f26try5n4pq7thttks3b9fs00000gn/T/ipykernel_44868/776011527.py:33: FutureWarning:

ChainedAssignme

In [66]:
df.reset_index(inplace=True)
df['date'] = pd.to_datetime(df['date'])
df.head(5)

index                date  counts  hourly_mov_average
0      0 2023-08-15 23:00:00  4851.0              4851.0
1      1 2023-08-16 00:00:00  6080.0              5465.5
2      2 2023-08-16 01:00:00  6142.0              5691.0
3      3 2023-08-16 02:00:00  5981.0              5763.5
4      4 2023-08-16 03:00:00  5675.0              5745.8

In [7]:
# Extract environment variables
load_dotenv()
DBNAME=getenv('DBNAME')
DBUSER=getenv('DBUSER')
DBHOST=getenv('DBHOST')
DBPORT=getenv('DBPORT')
DBPWRD=getenv('DBPWRD')

In [8]:
try:
    engine = create_engine(
        url="postgresql://{0}:{1}@{2}:{3}/{4}".format(
            DBUSER, DBPWRD, DBHOST, DBPORT, DBNAME
        )
    )
    print('Connected to muon database successfully')
except:
    print('Unable to connect to muon database')

try:
    conn = psycopg2.connect(f"dbname={DBNAME} user={DBUSER} host={DBHOST} port={DBPORT} password={DBPWRD}")
    print('Connected to muon database successfully')
except:
    print('Unable to connect to muon database')
cur = conn.cursor()

df.to_sql(
    con=engine, name=f'{detector_name}', if_exists='replace', index_label='date')
print('Table sent to DB successfully')

# Make primary key for table via PSYCOPG2
cur = conn.cursor()
cur.execute(f"""ALTER TABLE {detector_name} ADD PRIMARY KEY (date)""")
conn.commit()
cur.close()
print('Query for primary key sent successfully')

Connected to muon database successfully
Connected to muon database successfully
Table sent to DB successfully
Query for primary key sent successfully


In [6]:
df.sort_index(inplace=True)
# Calculate hourly moving average
df['hourly_mov_average'] = df['counts'].rolling(window='24h').mean()

In [7]:
''' 
The Percentage Change quantifies the change from one number to another 
and expresses the change as an increase or decrease.

    i.e.: 10 apples to 20 apples change = 100% increase (change)

Percentage change equals the change in value divided by the 
absolute value of the original value, multiplied by 100.

    i.e.: (V2 - V1)/ |V1|  * 100

For purposes of this calculation, our V2 is the mean of the counts of muons

'''
df['counts_pct'] = ((df['counts'] - df['counts'].mean()) / df['counts'].mean() * 100)
wdf['temp_pct']=0.2*((wdf['temp_in_f'] - wdf['temp_in_f'].mean())/ wdf['temp_in_f'].mean()*100)
wdf['alti_press_pct'] = 5*((wdf['alti_pressure'] - wdf['alti_pressure'].mean()) / wdf['alti_pressure'].mean() * 100)
wdf['sea_l_press_pct'] = ((wdf['sea_l_pressure_millibar'] - wdf['sea_l_pressure_millibar'].mean()) / wdf['sea_l_pressure_millibar'].mean() * 100)
# Change/delta of counts, pressure and temp
df['delta_counts'] = np.log(df['counts'] / df['counts'].mean())
wdf['delta_temp'] = wdf['temp_in_f'] - wdf['temp_in_f'].mean()
wdf['delta_alti_pressure'] = wdf['alti_pressure'] - wdf['alti_pressure'].mean()
wdf['delta_sea_l_pressure'] = wdf['sea_l_pressure_millibar'] - wdf['sea_l_pressure_millibar'].mean()

In [79]:
df.head(5)

counts  hourly_mov_average  counts_pct  delta_counts
date                                                                     
2023-08-15 23:00:00     NaN                 NaN         NaN           NaN
2023-08-16 00:00:00  6080.0         6080.000000  -16.940524     -0.185613
2023-08-16 01:00:00  6142.0         6111.000000  -16.093536     -0.175468
2023-08-16 02:00:00  5981.0         6067.666667  -18.292973     -0.202030
2023-08-16 03:00:00  5675.0         5969.500000  -22.473269     -0.254547

In [80]:
df.tail(2)

counts  hourly_mov_average  counts_pct  delta_counts
date                                                                     
2024-08-24 16:00:00  7407.0         7454.708333    1.187753      0.011808
2024-08-24 17:00:00  7566.0         7459.666667    3.359868      0.033047

In [81]:
wdf.head(2)

temp_in_f  sea_l_pressure_millibar  alti_pressure  \
date                                                                     
2023-08-15 23:00:00       89.6                      NaN          29.77   
2023-08-16 00:00:00       87.8                      NaN          29.77   

                     temp_pct  alti_press_pct  sea_l_press_pct  delta_temp  \
date                                                                         
2023-08-15 23:00:00  0.919829       -0.894395              NaN    3.939644   
2023-08-16 00:00:00  0.499564       -0.894395              NaN    2.139644   

                     delta_alti_pressure  delta_sea_l_pressure  
date                                                            
2023-08-15 23:00:00            -0.053348                   NaN  
2023-08-16 00:00:00            -0.053348                   NaN

In [179]:
df.index = df.index.tz_localize(None)

In [264]:
merged_dfs = df.merge(wdf, how='left', left_index=True, right_index=True)
merged_dfs.head(3)

counts  hourly_mov_average  counts_pct  delta_counts  \
date                                                                        
2024-05-01 15:00:00  5118.0         5118.000000    1.365390      0.013562   
2024-05-01 16:00:00  5063.0         5090.500000    0.276079      0.002757   
2024-05-01 17:00:00  4973.0         5051.333333   -1.506431     -0.015179   

                     temp_in_f  sea_l_pressure_millibar  alti_pressure  \
date                                                                     
2024-05-01 15:00:00       87.8                      NaN          29.74   
2024-05-01 16:00:00       86.0                      NaN          29.74   
2024-05-01 17:00:00        NaN                      NaN            NaN   

                     temp_pct  alti_press_pct  sea_l_press_pct  delta_temp  \
date                                                                         
2024-05-01 15:00:00  1.925576       -3.163181              NaN    7.710883   
2024-05-01 16:00:00  1.476077       -3.163181              NaN    5.910883   
2024-05-01 17:00:00       NaN             NaN              NaN         NaN   

                     delta_alti_pressure  delta_sea_l_pressure  
date                                                            
2024-05-01 15:00:00            -0.189344                   NaN  
2024-05-01 16:00:00            -0.189344                   NaN  
2024-05-01 17:00:00                  NaN                   NaN

In [124]:
fig1 = go.Figure(
    [   # Offline
        go.Scatter(
            x=df.index,
            y=df['counts'],
            name='Offline',
            line=dict(dash='dash', color='red', width=0.5),
            connectgaps=True
        ),
        # Raw Muon counts
        go.Scatter(
            x=df.index,
            y=df['counts'],
            name='Hourly Muon Counts',
            line=dict(color='red', width=2)
        ),
        # Hourly average
        go.Scatter(
            x=df.index,
            y=df['hourly_mov_average'],
            name='Hourly Counts Moving Ave.',
            line=dict(color='blue', width=2)
        ),
    ]
)
fig1.update_layout(
        title = {
            'text': f'{detector_name_og} : Real Time Cosmic Muon Monitor (Updated Daily)',
            'x':0.5,
            'y':0.99,
            'xanchor':'center',
            'yanchor':'top',
            'font_color':"#002379",
            'font_size':15
        },
        height=280,
        margin=dict(l=0, r=0, t=25, b=0),
    )

In [8]:
# Create a figure
fig = go.Figure(
    [   # Offline
        go.Scatter(
            x=df.index,
            y=df['counts_pct'],
            name='Offline',
            line=dict(dash='dash', color='red', width=0.5),
            connectgaps=True
        ),
        # Raw Muon counts
        go.Scatter(
            x=df.index,
            y=df['counts_pct'],
            name='Muon Counts % Change',
            line=dict(color='red', width=1)
        ),
        # temperature
        go.Scatter(
            x=wdf.index,
            y=wdf['temp_pct'],
            name='Temp(°F) % Change',
            line=dict(color='green', width=1),
            connectgaps=True
        ),
        # Altitude pressure
        go.Scatter(
            x=wdf.index,
            y=wdf['alti_press_pct'],
            name='Alt. Pressure % Change',
            line=dict(color='blue', width=1),
            connectgaps=True
        ),
    ]
)

In [9]:
if not pd.isna(wdf['sea_l_pressure_millibar']).all():
    print('True')
    fig.add_trace(
        # Sea level pressure
        go.Scatter(
            x=wdf.index,
            y=wdf['sea_l_press_pct'],
            name='Sea Level Press % Change',
            line=dict(color='orange', width=1)
        ),
    )

In [10]:
print('fig type: ', type(fig))
fig.update_layout(
    title = {
        'text': f'{detector_name_og} : Real Time Cosmic Muon Monitor (Updated Daily)',
        'x':0.5,
        'y':0.99,
        'xanchor':'center',
        'yanchor':'top',
        'font_color':"#002379",
        'font_size':15
    },
    height=280,
    margin=dict(l=0, r=0, t=25, b=0),
)

fig type:  <class 'plotly.graph_objs._figure.Figure'>
